In [ ]:
%pip install gradio
%pip install git+https://github.com/tensorflow/docs

  Cloning https://github.com/tensorflow/docs to c:\users\pc\appdata\local\temp\pip-req-build-cktlp7ez
  Resolved https://github.com/tensorflow/docs to commit 18c3a45517af27c8513e165b8a52e6bbc1204b99
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'


  Running command git clone --filter=blob:none --quiet https://github.com/tensorflow/docs 'C:\Users\PC\AppData\Local\Temp\pip-req-build-cktlp7ez'


In [2]:
# -*- coding: utf-8 -*-
"""🎬 Keras Video Classification CNN-RNN model

Spaces for showing the model usage.

Author:
    - Thomas Chaigneau @ChainYo
"""
import os
import cv2

import gradio as gr
import numpy as np

from tensorflow import keras

from tensorflow_docs.vis import embed

from huggingface_hub import from_pretrained_keras

c:\Users\PC\AppData\Local\Programs\Python\Python310\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
%mkdir Samples

A subdirectory or file Samples already exists.


In [18]:
# Kích thước ảnh đầu vào và số lượng đặc trưng
IMG_SIZE = 224
NUM_FEATURES = 2048

# Tải mô hình CNN-RNN từ HuggingFace
model = from_pretrained_keras("keras-io/video-classification-cnn-rnn")

# Tạo danh sách video ví dụ từ thư mục Samples
samples = []
for file in os.listdir("Samples"):
    tag = file.split("_")[1]
    samples.append([f"samples/{file}"])

# Cắt phần hình vuông ở trung tâm frame
def crop_center_square(frame):
    y, x = frame.shape[0:2]
    min_dim = min(y, x)
    start_x = (x // 2) - (min_dim // 2)
    start_y = (y // 2) - (min_dim // 2)
    return frame[start_y : start_y + min_dim, start_x : start_x + min_dim]

# Đọc video và xử lý từng frame
def load_video(path, max_frames=0, resize=(IMG_SIZE, IMG_SIZE)):
    cap = cv2.VideoCapture(path)
    frames = []
    try:
        while True:
            ret, frame = cap.read()
            if not ret:
                break
            frame = crop_center_square(frame)
            frame = cv2.resize(frame, resize)
            frame = frame[:, :, [2, 1, 0]]
            frames.append(frame)

            if len(frames) == max_frames:
                break
    finally:
        cap.release()
    return np.array(frames)

# Xây dựng mô hình trích xuất đặc trưng (InceptionV3)
def build_feature_extractor():
    feature_extractor = keras.applications.InceptionV3(
        weights="imagenet",
        include_top=False,
        pooling="avg",
        input_shape=(IMG_SIZE, IMG_SIZE, 3),
    )
    preprocess_input = keras.applications.inception_v3.preprocess_input

    inputs = keras.Input((IMG_SIZE, IMG_SIZE, 3))
    preprocessed = preprocess_input(inputs)

    outputs = feature_extractor(preprocessed)
    return keras.Model(inputs, outputs, name="feature_extractor")

# Tạo feature extractor 1 lần
feature_extractor = build_feature_extractor()

# Trích xuất đặc trưng cho từng frame của video
def prepare_video(frames, max_seq_length: int = 20):
    frames = frames[None, ...]
    frame_mask = np.zeros(shape=(1, max_seq_length,), dtype="bool")
    frame_features = np.zeros(shape=(1, max_seq_length, NUM_FEATURES), dtype="float32")

    for i, batch in enumerate(frames):
        video_length = batch.shape[0]
        length = min(max_seq_length, video_length)
        for j in range(length):
            frame_features[i, j, :] = feature_extractor.predict(batch[None, j, :])
        frame_mask[i, :length] = 1  # 1 = not masked, 0 = masked

    return frame_features, frame_mask

# Dự đoán hành động từ video
def sequence_prediction(path):
    class_vocab = ["CricketShot", "PlayingCello", "Punch", "ShavingBeard", "TennisSwing"]

    frames = load_video(path)
    frame_features, frame_mask = prepare_video(frames)
    probabilities = model.predict([frame_features, frame_mask])[0]

    preds = {}
    for i in np.argsort(probabilities)[::-1]:
        preds[class_vocab[i]] = float(probabilities[i])
    return preds

# HTML mô tả bên dưới app
article = article = "<div style='text-align: center;'><a href='https://github.com/ChainYo' target='_blank'>Space by Thomas Chaigneau</a><br><a href='https://keras.io/examples/vision/video_classification/' target='_blank'>Keras example by Sayak Paul</a></div>"

# Tạo giao diện Gradio
app = gr.Interface(
    fn=sequence_prediction,
    inputs=[gr.Video(label="Video")],
    outputs=gr.Label(label="Prediction"),
    title="Keras Video Classification with CNN-RNN",
    description="Video classification demo using CNN-RNN based model.",
    article=article,
    examples=samples
)

# Khởi chạy ứng dụng
app.launch()



Fetching 11 files:   0%|          | 0/11 [00:00<?, ?it/s]

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://06f7718827d3f617a0.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
